In [32]:
import numpy as np
import cv2
import os
import random
import tensorflow as tf
from tensorflow.keras.callbacks import Callback
from tqdm import tqdm
from tensorflow.keras import layers, Model, optimizers


In [33]:
def load_images_from_folder(folder):
    images = []
    for filename in os.listdir(folder):
        file_path = os.path.join(folder, filename)
        if os.path.isdir(file_path):
            continue  # Skip directories
        if not file_path.endswith(('.png', '.jpg', '.jpeg')):
            continue  # Skip non-image files
        
        img = cv2.imread(file_path, cv2.IMREAD_GRAYSCALE)
        if img is not None:
            images.append(img)
    return images

In [34]:
def generate_pairs(dataset_dir):
    pairs = []
    labels = []
    persons = os.listdir(dataset_dir)
    persons = [person for person in persons if os.path.isdir(os.path.join(dataset_dir, person))]

    for person in persons:
        person_dir = os.path.join(dataset_dir, person)
    
       
        images = load_images_from_folder(person_dir)
      
        if len(images) < 2:
            continue  
        
        # Positive pairs
        for i in range(len(images)):
            for j in range(i + 1, len(images)):
                pairs.append((images[i], images[j]))
                labels.append(1)
                
        # Negative pairs
        other_persons = [p for p in persons if p != person]
        for i in range(len(images)):
            while True:
                other_person = random.choice(other_persons)
                other_person_dir = os.path.join(dataset_dir, other_person)
                try:
                    other_images = load_images_from_folder(other_person_dir)
                except NotADirectoryError:
                    other_images = []
                if other_images:
                    break  # Ensure we get a non-empty list of images
            if not other_images:
                continue  # Skip if other_images is empty
            
            other_image = random.choice(other_images)
            pairs.append((images[i], other_image))
            labels.append(0)
                
    return pairs, labels



In [35]:
train_dir='/Users/apoorvagayatrik/PerspectAIProj/processed_images/train_ds'
test_dir='/Users/apoorvagayatrik/PerspectAIProj/processed_images/test_ds'
val_dir='/Users/apoorvagayatrik/PerspectAIProj/processed_images/val_ds'

In [36]:
train_pairs, train_labels = generate_pairs(train_dir)
val_pairs, val_labels = generate_pairs(val_dir)
test_pairs, test_labels = generate_pairs(test_dir)

In [37]:
def create_siamese_network(input_shape):
    input = layers.Input(input_shape)
    x = layers.Conv2D(64, (7, 7), activation='relu', padding='same')(input)
    x = layers.MaxPooling2D(pool_size=(2, 2))(x)
    x = layers.Conv2D(128, (5, 5), activation='relu', padding='same')(x)
    x = layers.MaxPooling2D(pool_size=(2, 2))(x)
    x = layers.Conv2D(128, (3, 3), activation='relu', padding='same')(x)
    x = layers.MaxPooling2D(pool_size=(2, 2))(x)
    x = layers.Conv2D(256, (3, 3), activation='relu', padding='same')(x)
    x = layers.Flatten()(x)
    x = layers.Dense(4096, activation='sigmoid')(x)
    return Model(input, x)

In [39]:
class TqdmProgressCallback(Callback):
    def __init__(self, steps_per_epoch):
        super().__init__()
        self.steps_per_epoch = steps_per_epoch

    def on_epoch_begin(self, epoch, logs=None):
        self.progress_bar = tqdm(total=self.steps_per_epoch, desc=f'Epoch {epoch + 1}/{self.params["epochs"]}', unit='step')

    def on_batch_end(self, batch, logs=None):
        self.progress_bar.update(1)

    def on_epoch_end(self, epoch, logs=None):
        self.progress_bar.close()

# Determine steps per epoch
batch_size = 32
steps_per_epoch = len(train_pairs[0]) // batch_size

# Initialize the callback with steps per epoch
progress_callback = TqdmProgressCallback(steps_per_epoch)



In [40]:
input_shape = (64, 64, 1)  # Example input shape
base_network = create_siamese_network(input_shape)


In [41]:
input_a = layers.Input(shape=input_shape)
input_b = layers.Input(shape=input_shape)


In [42]:
encoded_a = base_network(input_a)
encoded_b = base_network(input_b)



In [43]:
L1_layer = layers.Lambda(lambda tensors: tf.abs(tensors[0] - tensors[1]))
L1_distance = L1_layer([encoded_a, encoded_b])

In [44]:
output = layers.Dense(1, activation='sigmoid')(L1_distance)


In [45]:
siamese_net = Model(inputs=[input_a, input_b], outputs=output)


In [46]:
siamese_net.compile(loss='binary_crossentropy', optimizer=optimizers.Adam(0.0001), metrics=['accuracy'])


In [47]:
def prepare_data(pairs, labels):
    pairs = np.array(pairs, dtype=np.float32)
    pairs = pairs / 255.0  # Normalize to [0, 1]
    labels = np.array(labels, dtype=np.float32)
    return pairs, labels

In [48]:
train_pairs, train_labels = prepare_data(train_pairs, train_labels)
val_pairs, val_labels = prepare_data(val_pairs, val_labels)
test_pairs, test_labels = prepare_data(test_pairs, test_labels)


In [49]:
train_pairs = [train_pairs[:, 0].reshape(-1, 64, 64, 1), train_pairs[:, 1].reshape(-1, 64, 64, 1)]
val_pairs = [val_pairs[:, 0].reshape(-1, 64, 64, 1), val_pairs[:, 1].reshape(-1, 64, 64, 1)]
test_pairs = [test_pairs[:, 0].reshape(-1, 64,64, 1), test_pairs[:, 1].reshape(-1, 64, 64, 1)]

In [51]:
from tensorflow.keras.callbacks import EarlyStopping
early_stopping = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)


In [52]:
history = siamese_net.fit(
    [train_pairs[0], train_pairs[1]], train_labels,
    validation_data=([val_pairs[0], val_pairs[1]], val_labels),
    batch_size=32,
    epochs=50,  # Larger number of epochs, relying on early stopping
    callbacks=[progress_callback, early_stopping]
)

Epoch 1/50: 0step [00:00, ?step/s]

Epoch 1/50


Epoch 1/50: 1step [00:08,  8.22s/step]

   1/2052 ━━━━━━━━━━━━━━━━━━━━ 4:40:43 8s/step - accuracy: 0.2188 - loss: 0.6933

Epoch 1/50: 2step [00:08,  3.68s/step]

...

2051/2052 ━━━━━━━━━━━━━━━━━━━━ 0s 521ms/step - accuracy: 0.9980 - loss: 0.0100

Epoch 6/50: 2052step [17:53,  2.07step/s]

2052/2052 ━━━━━━━━━━━━━━━━━━━━ 0s 521ms/step - accuracy: 0.9980 - loss: 0.0100

Epoch 6/50: 2052step [21:55,  1.56step/s]

2052/2052 ━━━━━━━━━━━━━━━━━━━━ 1316s 639ms/step - accuracy: 0.9980 - loss: 0.0100 - val_accuracy: 0.8543 - val_loss: 0.7971


In [54]:
from tensorflow.keras.models import load_model

# Assuming facenet_model is your trained model
siamese_net.save('siamese_model.keras')


In [23]:
import matplotlib.pyplot as plt
from tensorflow.keras.models import load_model
from tensorflow.keras.callbacks import History

In [53]:
test_loss, test_accuracy = siamese_net.evaluate([test_pairs[0], test_pairs[1]], test_labels)
print(f"Test Loss: {test_loss}")
print(f"Test Accuracy: {test_accuracy}")


1896/1896 ━━━━━━━━━━━━━━━━━━━━ 166s 86ms/step - accuracy: 0.9627 - loss: 0.1455
Test Loss: 0.1532735973596573
Test Accuracy: 0.9613234996795654


In [28]:
val_loss, val_accuracy = siamese_net.evaluate([val_pairs[0], val_pairs[1]], val_labels)
print(f"Test Loss: {val_loss}")
print(f"Test Accuracy: {val_accuracy}")


3219/3219 ━━━━━━━━━━━━━━━━━━━━ 287s 87ms/step - accuracy: 0.8590 - loss: 0.7713
Test Loss: 0.6743754744529724
Test Accuracy: 0.8565782904624939
